# Playing around with Machine to Machine API access

In [ ]:
import requests
from tqdm import tqdm

## Let's do some EagleEye setup

In [ ]:
import logging
logger = logging.getLogger()
logger.setLevel('INFO')

In [ ]:
from EagleEyev3 import *
from settings import config

In [ ]:
een = EagleEyev3(config)

In [ ]:
een.__version__

## Let's do some DB setup

In [ ]:
import sqlite3

In [ ]:
sqlite3.sqlite_version

In [ ]:
con = sqlite3.connect('instance/project.db')

In [ ]:
cur = con.cursor()

## Login as a user with their refresh_token and query their cameras

In [ ]:
if een:
    if een.refresh_token == None or een.refresh_token == '':
        # if you get out of sync, pull the refresh_token from the db to get the loop started
        result = cur.execute("select user.refresh_token from user where user.email = ?;", ("mcotton@mcottondesign.com",))
    
        for row in result:
            een.refresh_token = row[0]
    else:
        # een object and refresh_token appear to be good
        pass
else:
    logging.error('een object is None')

In [ ]:
_ = een.login_tokens(code=None, cascade=True, refresh_token=een.refresh_token)

In [ ]:
een.refresh_token

In [ ]:
een.current_user

In [ ]:
result = cur.execute("select user.refresh_token, user.id from user where user.email = ?;", (een.current_user['email'],))

for row in result:
    print(f"found user {een.current_user['email']}, updating refresh_token")
    print(row)
    print(een.refresh_token)
    print(f"update user set refresh_token = {een.refresh_token} where id == {row[1]};")
    cur.execute("update user set refresh_token = ? where id == ?;", (een.refresh_token, row[1]))
    con.commit()

In [ ]:
_ = een.get_list_of_cameras()

In [ ]:
een.cameras

In [ ]:
r2d2 = een.cameras[3]

In [ ]:
_ = r2d2.get_list_of_videos(start_timestamp=een.time_before(hours=24*1), end_timestamp=een.time_now())

In [ ]:
len(r2d2.videos)

## Download all the videos ##

In [ ]:
sql = '''SELECT
	download.id,
	download.url,
	camera.device_id,
	download.start_timestamp,
	download.end_timestamp,
	download.status
FROM
	camera
	JOIN download ON download.camera_id = camera.id
	JOIN USER ON camera.user_id = user.id
WHERE
	download.status == ?
	AND camera.id == ?;'''

In [ ]:
results = cur.execute(sql, ('new', 4))

for row in tqdm(results):
    fname = f"videos/{row[2]}/{row[2]}_{row[3]}-{row[4]}.mp4"
    print(f"{row[0]} - {row[5]}")
    r2d2.save_video_to_file(url=row[1], filename=fname)
    new_cur = con.cursor()
    new_cur.execute("update download set status = ? where download.id == ?;", ('done', row[0]))
    
    # less efficient to commit every iteration but it means I can watch the updates at the DB level
    con.commit()